#### `https://www.shiksha.com/online-courses/articles/text-pre-processing-for-spam-filtering/`

`https://www.shiksha.com/online-courses/articles/spam-filtering-using-bag-of-words/`

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
import string



from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.naive_bayes import BernoulliNB
from sklearn.metrics import accuracy_score

In [3]:
df = pd.read_csv("DataSets/full/index1.csv",header=None)
df

0
0       ham ../data/000/000
1       ham ../data/000/001
2       ham ../data/000/002
3       ham ../data/000/003
4       ham ../data/000/004
...                     ...
92184  spam ../data/307/086
92185  spam ../data/307/087
92186  spam ../data/307/088
92187  spam ../data/307/089
92188  spam ../data/307/090

[92189 rows x 1 columns]

In [4]:
df.rename(columns={0:'temp'},inplace=True)

In [5]:
df

temp
0       ham ../data/000/000
1       ham ../data/000/001
2       ham ../data/000/002
3       ham ../data/000/003
4       ham ../data/000/004
...                     ...
92184  spam ../data/307/086
92185  spam ../data/307/087
92186  spam ../data/307/088
92187  spam ../data/307/089
92188  spam ../data/307/090

[92189 rows x 1 columns]

In [6]:
df[['label','path']] = df['temp'].str.split(' ',1,expand=True)

C:\Users\91747\AppData\Local\Temp\ipykernel_1648\2128601247.py:1: FutureWarning: In a future version of pandas all arguments of StringMethods.split except for the argument 'pat' will be keyword-only.
  df[['label','path']] = df['temp'].str.split(' ',1,expand=True)


In [7]:
df

temp label             path
0       ham ../data/000/000   ham  ../data/000/000
1       ham ../data/000/001   ham  ../data/000/001
2       ham ../data/000/002   ham  ../data/000/002
3       ham ../data/000/003   ham  ../data/000/003
4       ham ../data/000/004   ham  ../data/000/004
...                     ...   ...              ...
92184  spam ../data/307/086  spam  ../data/307/086
92185  spam ../data/307/087  spam  ../data/307/087
92186  spam ../data/307/088  spam  ../data/307/088
92187  spam ../data/307/089  spam  ../data/307/089
92188  spam ../data/307/090  spam  ../data/307/090

[92189 rows x 3 columns]

In [8]:
df['label']

0         ham
1         ham
2         ham
3         ham
4         ham
         ... 
92184    spam
92185    spam
92186    spam
92187    spam
92188    spam
Name: label, Length: 92189, dtype: object

In [9]:
df['path']

0        ../data/000/000
1        ../data/000/001
2        ../data/000/002
3        ../data/000/003
4        ../data/000/004
              ...       
92184    ../data/307/086
92185    ../data/307/087
92186    ../data/307/088
92187    ../data/307/089
92188    ../data/307/090
Name: path, Length: 92189, dtype: object

In [10]:
df.drop('temp',axis=1,inplace=True)

In [11]:
df

label             path
0       ham  ../data/000/000
1       ham  ../data/000/001
2       ham  ../data/000/002
3       ham  ../data/000/003
4       ham  ../data/000/004
...     ...              ...
92184  spam  ../data/307/086
92185  spam  ../data/307/087
92186  spam  ../data/307/088
92187  spam  ../data/307/089
92188  spam  ../data/307/090

[92189 rows x 2 columns]

   ### Converting the `ham` and `spam` into numbers
   
   ##### Let spam = 1 and ham = 0

In [12]:
def convert(value):
    if(value == 'spam'):
        return 1
    else:
        return 0

In [13]:
df['label'] = df['label'].map(convert)

In [14]:
df

label             path
0          0  ../data/000/000
1          0  ../data/000/001
2          0  ../data/000/002
3          0  ../data/000/003
4          0  ../data/000/004
...      ...              ...
92184      1  ../data/307/086
92185      1  ../data/307/087
92186      1  ../data/307/088
92187      1  ../data/307/089
92188      1  ../data/307/090

[92189 rows x 2 columns]

In [15]:
df['label'].value_counts()

1    52790
0    39399
Name: label, dtype: int64

In [16]:
df_sorted = df.sort_values('label')

In [17]:
df_sorted

label             path
0          0  ../data/000/000
41683      0  ../data/138/285
41684      0  ../data/138/286
41685      0  ../data/138/287
41686      0  ../data/138/288
...      ...              ...
54929      1  ../data/183/031
54930      1  ../data/183/032
54931      1  ../data/183/033
11023      1  ../data/036/225
92188      1  ../data/307/090

[92189 rows x 2 columns]

In [18]:
# Checking from which index 1 starts ...now we can take equal amount of spam mails and not spam(ie. ham) mails...and train our 
# model
df.iloc[39398]['label'],df.iloc[39399]['label']

(0, 1)

In [19]:
df_spam = df_sorted[39399:39899]
df_ham = df_sorted[38898:39398]
len(df_spam),len(df_ham)

(500, 500)

In [20]:
df_spam

label             path
1637       1  ../data/005/137
76594      1  ../data/255/096
73139      1  ../data/243/241
1636       1  ../data/005/136
76593      1  ../data/255/095
...      ...              ...
73013      1  ../data/243/115
73014      1  ../data/243/116
75691      1  ../data/252/093
76334      1  ../data/254/136
73685      1  ../data/245/187

[500 rows x 2 columns]

In [21]:
df_ham

label             path
24291      0  ../data/080/293
3946       0  ../data/013/046
13822      0  ../data/046/024
24265      0  ../data/080/267
24206      0  ../data/080/208
...      ...              ...
13466      0  ../data/044/268
13461      0  ../data/044/263
12279      0  ../data/040/281
23225      0  ../data/077/127
23426      0  ../data/078/028

[500 rows x 2 columns]

In [22]:
df_spam = df_spam.reset_index(drop=True)

In [23]:
df_ham = df_ham.reset_index(drop=True)

In [24]:
df_spam

label             path
0        1  ../data/005/137
1        1  ../data/255/096
2        1  ../data/243/241
3        1  ../data/005/136
4        1  ../data/255/095
..     ...              ...
495      1  ../data/243/115
496      1  ../data/243/116
497      1  ../data/252/093
498      1  ../data/254/136
499      1  ../data/245/187

[500 rows x 2 columns]

In [25]:
df_ham

label             path
0        0  ../data/080/293
1        0  ../data/013/046
2        0  ../data/046/024
3        0  ../data/080/267
4        0  ../data/080/208
..     ...              ...
495      0  ../data/044/268
496      0  ../data/044/263
497      0  ../data/040/281
498      0  ../data/077/127
499      0  ../data/078/028

[500 rows x 2 columns]

In [26]:
df_spam['label'].value_counts(),df_ham['label'].value_counts()

(1    500
 Name: label, dtype: int64,
 0    500
 Name: label, dtype: int64)

## Combining the two dataframes


In [27]:
new_df = pd.concat([df_ham,df_spam])
new_df

label             path
0        0  ../data/080/293
1        0  ../data/013/046
2        0  ../data/046/024
3        0  ../data/080/267
4        0  ../data/080/208
..     ...              ...
495      1  ../data/243/115
496      1  ../data/243/116
497      1  ../data/252/093
498      1  ../data/254/136
499      1  ../data/245/187

[1000 rows x 2 columns]

In [28]:
new_df = new_df.sample(frac=1).reset_index(drop=True)
new_df

label             path
0        0  ../data/082/117
1        1  ../data/007/143
2        1  ../data/252/079
3        0  ../data/044/269
4        1  ../data/004/207
..     ...              ...
995      1  ../data/004/259
996      0  ../data/077/271
997      0  ../data/077/130
998      1  ../data/258/190
999      1  ../data/255/107

[1000 rows x 2 columns]

## Getting our respective email files from the paths to our dataframe

In [29]:
# new_df['path'].str.split('/',1)[0][1]

In [30]:
new_df

label             path
0        0  ../data/082/117
1        1  ../data/007/143
2        1  ../data/252/079
3        0  ../data/044/269
4        1  ../data/004/207
..     ...              ...
995      1  ../data/004/259
996      0  ../data/077/271
997      0  ../data/077/130
998      1  ../data/258/190
999      1  ../data/255/107

[1000 rows x 2 columns]

In [31]:
def seperate(temp):
    return temp[1]

In [32]:
new_df['paths'] = new_df['path'].str.split('/',1)
new_df['paths'] = new_df['paths'].map(seperate)
new_df

C:\Users\91747\AppData\Local\Temp\ipykernel_1648\263685750.py:1: FutureWarning: In a future version of pandas all arguments of StringMethods.split except for the argument 'pat' will be keyword-only.
  new_df['paths'] = new_df['path'].str.split('/',1)


label             path         paths
0        0  ../data/082/117  data/082/117
1        1  ../data/007/143  data/007/143
2        1  ../data/252/079  data/252/079
3        0  ../data/044/269  data/044/269
4        1  ../data/004/207  data/004/207
..     ...              ...           ...
995      1  ../data/004/259  data/004/259
996      0  ../data/077/271  data/077/271
997      0  ../data/077/130  data/077/130
998      1  ../data/258/190  data/258/190
999      1  ../data/255/107  data/255/107

[1000 rows x 3 columns]

In [33]:
def read_file(paths):
    path = 'DataSets' + '/' + paths
    with open(path,'r',encoding='utf-8',errors='ignore') as file:
        return file.readlines()

In [34]:
new_df['file_contents'] = new_df['paths'].map(read_file)


In [35]:
new_df

label             path         paths  \
0        0  ../data/082/117  data/082/117   
1        1  ../data/007/143  data/007/143   
2        1  ../data/252/079  data/252/079   
3        0  ../data/044/269  data/044/269   
4        1  ../data/004/207  data/004/207   
..     ...              ...           ...   
995      1  ../data/004/259  data/004/259   
996      0  ../data/077/271  data/077/271   
997      0  ../data/077/130  data/077/130   
998      1  ../data/258/190  data/258/190   
999      1  ../data/255/107  data/255/107   

                                         file_contents  
0    [Received: from NAHOU-MSMBX07V.corp.enron.com ...  
1    [Recieved: from nahou-mscnx06p.corp.enron.com ...  
2    [Received: from nahou-mscnx06p.corp.enron.com ...  
3    [Received: from nahou-mscnx06p.corp.enron.com ...  
4    [Recieved: from nahou-mscnx06p.corp.enron.com ...  
..                                                 ...  
995  [Recieved: from nahou-mscnx06p.corp.enron.com ...  
996  [Received: from nahou-mscnx03p.corp.enron.com ...  
997  [Received: from NAHOU-MSMBX07V.corp.enron.com ...  
998  [Received: from nahou-mscnx06p.corp.enron.com ...  
999  [Received: from nahou-mscnx06p.corp.enron.com ...  

[1000 rows x 4 columns]

In [36]:
new_df.drop('paths',axis=1,inplace=True)

In [37]:
new_df

label             path                                      file_contents
0        0  ../data/082/117  [Received: from NAHOU-MSMBX07V.corp.enron.com ...
1        1  ../data/007/143  [Recieved: from nahou-mscnx06p.corp.enron.com ...
2        1  ../data/252/079  [Received: from nahou-mscnx06p.corp.enron.com ...
3        0  ../data/044/269  [Received: from nahou-mscnx06p.corp.enron.com ...
4        1  ../data/004/207  [Recieved: from nahou-mscnx06p.corp.enron.com ...
..     ...              ...                                                ...
995      1  ../data/004/259  [Recieved: from nahou-mscnx06p.corp.enron.com ...
996      0  ../data/077/271  [Received: from nahou-mscnx03p.corp.enron.com ...
997      0  ../data/077/130  [Received: from NAHOU-MSMBX07V.corp.enron.com ...
998      1  ../data/258/190  [Received: from nahou-mscnx06p.corp.enron.com ...
999      1  ../data/255/107  [Received: from nahou-mscnx06p.corp.enron.com ...

[1000 rows x 3 columns]

## Adding new columns like of Subject,From,Cc,Bcc,Date ...in our dataframe

In [38]:
new_df['file_contents'][0][6]

'Content-Transfer-Encoding: binary\n'

In [39]:
lst_lst = new_df['file_contents'].tolist()
lst_lst

[['Received: from NAHOU-MSMBX07V.corp.enron.com ([192.168.110.98]) by NAHOU-MSMBX01V.corp.enron.com with Microsoft SMTPSVC(5.0.2195.2966);\n',
  '\t Tue, 16 Oct 2001 09:21:42 -0500\n',
  'X-MimeOLE: Produced By Microsoft Exchange V6.0.4712.0\n',
  'content-class: urn:content-classes:message\n',
  'MIME-Version: 1.0\n',
  'Content-Type: text/plain;\n',
  'Content-Transfer-Encoding: binary\n',
  'Subject: FW: SUN1017.xls\n',
  'Date: Tue, 16 Oct 2001 09:21:40 -0500\n',
  'Message-ID: <180973634378954E8B265F4485D159541878A6@NAHOU-MSMBX07V.corp.enron.com>\n',
  'X-MS-Has-Attach: \n',
  'X-MS-TNEF-Correlator: <180973634378954E8B265F4485D159541878A6@NAHOU-MSMBX07V.corp.enron.com>\n',
  'Thread-Topic: SUN1017.xls\n',
  'Thread-Index: AcFWQsDI79y9+MI1EdWxIgBQi+MJ2QACwMeg\n',
  'From: "Callans, Nancy" <Nancy.Callans@ENRON.com>\n',
  'To: "DL-ETS Gas Controllers" <DL-ETSGasControllers@ENRON.com>\n',
  'Return-Path: Nancy.Callans@ENRON.com\n',
  '\n',
  '\n',
  '\n',
  ' -----Original Message----

In [40]:
print(lst_lst[0][0])

Received: from NAHOU-MSMBX07V.corp.enron.com ([192.168.110.98]) by NAHOU-MSMBX01V.corp.enron.com with Microsoft SMTPSVC(5.0.2195.2966);



In [41]:
"from" in lst_lst[0][0]

True

In [42]:
len(new_df)

1000

In [43]:
substring = 'Subject'
sub_index = []
for i in range(0,1000):
    # TO ensure if there is no subject in the mail...then append a different number in the list...because some mail may dont have 
    # subject then...if we ignore this case and later try to add this subject column to our new_df then we will get error...because
    # of unequal length
    flag = True
    for string in lst_lst[i]:
        if substring in string:
            index = lst_lst[i].index(string)
            sub_index.append(index)
            flag = False
            break
    if flag :
        # If our flag still remains true which means we are unable to find the subject in mail...in that case...just append -1
        sub_index.append(-1)
        
print(sub_index)

[7, 18, 13, 31, 17, 18, 13, 7, 13, 18, 15, 7, 16, 13, 11, 13, 7, 7, 65, 18, 2, 12, 15, 7, 15, 10, 7, 15, 11, 17, 7, 7, 16, 20, 15, 7, 17, 13, 22, 7, 17, 7, 21, 7, 13, 23, 22, 23, 13, 17, 13, 17, 7, 18, 25, 13, 12, 17, 7, 7, 7, 13, 15, 14, 4, 7, 13, 24, 7, 17, 19, 13, 22, 7, 13, 20, 4, 7, 17, 11, 7, 10, 12, 14, 13, 19, 15, 15, 7, 19, 8, 15, 18, 28, 15, 13, 15, 7, 12, 7, 11, 7, 12, 24, 21, 15, 12, 16, 13, 15, 17, 13, 13, 4, 65, 15, 12, 24, -1, 7, 15, 13, 7, 6, 15, 17, 27, 13, 13, 15, 15, 32, 39, 3, 12, 20, 7, 13, 18, 17, 21, 7, 19, 13, 15, 13, 7, 15, 7, 13, 7, 15, 13, 7, 13, 13, 7, 10, 8, 19, 7, 10, 19, 7, 7, 14, 17, 25, 13, 23, 7, 13, 4, 15, 15, 15, 15, 7, 13, 16, 7, 20, 7, 15, 16, 28, 7, 17, 7, 13, 5, 7, 15, 19, 18, 16, 7, 11, 7, 7, 15, 10, 20, 15, 21, 7, 4, 13, 7, 13, 13, 7, 17, 21, 24, 12, 21, 17, 7, 15, 10, 15, 7, 20, 16, 7, 17, 13, 7, 16, 18, 15, 4, 18, 13, 7, 16, 15, 7, 13, 13, 16, 43, 7, 7, 20, 7, 19, 7, 13, 17, 18, 17, 7, 20, 20, 7, 20, 13, 13, 11, 13, 7, 19, 17, 20, 22, 19, 13,

In [44]:
# Checking if the index returned is correct
(new_df['file_contents'][0][16],
new_df['file_contents'][1][17],
new_df['file_contents'][2][22],
new_df['file_contents'][3][13],
new_df['file_contents'][4][17])

('Return-Path: Nancy.Callans@ENRON.com\n',
 'To: ericperss@web.de\n',
 '</head>\n',
 '          (LISTSERV-TCP/IP release 1.8c) with spool id 0449 for\n',
 'Subject: Marci\n')

In [45]:
# Now we got the index in every mail...where the Subject comes...so we know will retrieve this Subject and add to our dataframe..
subject=[]
for i in range(0,1000):
    if(sub_index[i] != -1):
        subject.append(lst_lst[i][sub_index[i]][9:-1])
    # here we only want the subject that's why we trim our result from lst_lst[i][temp[i]] from 9 to -1...because....from
    # every subject line...our real subject content starts from index 9 ...and we dont want that new line chararcter that's why
    # we use -1
    else:
        subject.append('-1');

    
print(subject)

['FW: SUN1017.xls', 'PRIVATE', 'Fw:', 'OASIS Posting -  Revised Final Real Power Losses', 'Marci', 'Updated Agenda and attachment', 'Miracle protein to help you', 'Oneok Recap Oct 13th.', 'Read this before purchasing penis enlarge products!', '=?utf-8?B?TG9va2luZyBmb3IgY2hlYXAgaGlnaC1xdWFsaXR5IHNvZnR3YXJlPyAgY3JlYWt5IHJlcHVnbmFudA==?=', 'ڳ ܱ  ȭн ü Ȥ CD 帳ϴ!!! lcgvveknphjep', 'RE: Path Manager Rewrite', 'Thanks for the informative session', 'Penis Growth Patches are here!', 'Small IR-Led Cameras', 'ATT//:URGENT ATTENTION', 'Oct. 11 FERC meeting discussion items', 'Location change - Sun Devil weekly meeting ', 'Contact change - Tim Sarhatt', 'CESG Annual Retreat', 'PG&E Core - ECC Master Gas Purchase and Sales Agreement ', 'Job offer', 'Get the instant VIP Advantage Visa card now ', 'FW: Setoff and ISDA Section 7(b) Transfer Provision; Comments on New Draft of Master Netting', 'RE: No truer words were ever spoken', 'Presenting Credit Loans hassle free', 'FW: Confidentiality Agreement', '1

In [46]:
# NOW adding this above subject list to our dataframe as our column
new_df['Subject'] = subject

In [47]:
new_df

label             path  \
0        0  ../data/082/117   
1        1  ../data/007/143   
2        1  ../data/252/079   
3        0  ../data/044/269   
4        1  ../data/004/207   
..     ...              ...   
995      1  ../data/004/259   
996      0  ../data/077/271   
997      0  ../data/077/130   
998      1  ../data/258/190   
999      1  ../data/255/107   

                                         file_contents  \
0    [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
1    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
2    [Received: from nahou-mscnx06p.corp.enron.com ...   
3    [Received: from nahou-mscnx06p.corp.enron.com ...   
4    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
..                                                 ...   
995  [Recieved: from nahou-mscnx06p.corp.enron.com ...   
996  [Received: from nahou-mscnx03p.corp.enron.com ...   
997  [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
998  [Received: from nahou-mscnx06p.corp.enron.com ...   
999  [Received: from nahou-mscnx06p.corp.enron.com ...   

                                               Subject  
0                                      FW: SUN1017.xls  
1                                              PRIVATE  
2                                                  Fw:  
3     OASIS Posting -  Revised Final Real Power Losses  
4                                                Marci  
..                                                 ...  
995                                 are you suffering   
996                         RE: Off-site Presentations  
997                                           RE: Pira  
998  Need Protection against SARS viruses? This may...  
999                       What you've been looking for  

[1000 rows x 4 columns]

In [48]:
# Now we have to repeat the same process for From, Date, To, Cc, Bcc...etc


In [49]:
# # Finding the common words in first two mails...

    

# # Read the contents of the first file
# with open('trec05p-1/data/021/061', 'r') as f:
#     file1_contents = f.read()

# # Read the contents of the second file
# with open('trec05p-1/data/004/133', 'r') as f:
#     file2_contents = f.read()

# # Convert the contents of each file to sets of words
# file1_words = set(file1_contents.split())
# file2_words = set(file2_contents.split())

# # Find the common words
# common_words = file1_words.intersection(file2_words)

# print('Common words:', common_words)

In [50]:
new_df['paths'] = new_df['path'].str.split('/',1)
new_df['paths'] = new_df['paths'].map(seperate)
new_df

C:\Users\91747\AppData\Local\Temp\ipykernel_1648\263685750.py:1: FutureWarning: In a future version of pandas all arguments of StringMethods.split except for the argument 'pat' will be keyword-only.
  new_df['paths'] = new_df['path'].str.split('/',1)


label             path  \
0        0  ../data/082/117   
1        1  ../data/007/143   
2        1  ../data/252/079   
3        0  ../data/044/269   
4        1  ../data/004/207   
..     ...              ...   
995      1  ../data/004/259   
996      0  ../data/077/271   
997      0  ../data/077/130   
998      1  ../data/258/190   
999      1  ../data/255/107   

                                         file_contents  \
0    [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
1    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
2    [Received: from nahou-mscnx06p.corp.enron.com ...   
3    [Received: from nahou-mscnx06p.corp.enron.com ...   
4    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
..                                                 ...   
995  [Recieved: from nahou-mscnx06p.corp.enron.com ...   
996  [Received: from nahou-mscnx03p.corp.enron.com ...   
997  [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
998  [Received: from nahou-mscnx06p.corp.enron.com ...   
999  [Received: from nahou-mscnx06p.corp.enron.com ...   

                                               Subject         paths  
0                                      FW: SUN1017.xls  data/082/117  
1                                              PRIVATE  data/007/143  
2                                                  Fw:  data/252/079  
3     OASIS Posting -  Revised Final Real Power Losses  data/044/269  
4                                                Marci  data/004/207  
..                                                 ...           ...  
995                                 are you suffering   data/004/259  
996                         RE: Off-site Presentations  data/077/271  
997                                           RE: Pira  data/077/130  
998  Need Protection against SARS viruses? This may...  data/258/190  
999                       What you've been looking for  data/255/107  

[1000 rows x 5 columns]

In [51]:
file_name = 'DataSets' + '/' + new_df['paths'][0]
with open(file_name,'r',encoding='utf-8',errors='ignore') as f:
    words = set(f.read().split())
words

{'"Callans,',
 '"DL-ETS',
 '"Rodenburg,',
 '([192.168.110.98])',
 '-',
 '-----Original',
 '-0500',
 '09:21:40',
 '09:21:42',
 '1.0',
 '16',
 '16,',
 '2001',
 '7:59',
 '<180973634378954E8B265F4485D159541878A6@NAHOU-MSMBX07V.corp.enron.com>',
 '<DL-ETSGasControllers@ENRON.com>',
 '<Nancy.Callans@ENRON.com>',
 '<erodenbu@UtiliCorp.com>@ENRON',
 'AM',
 'AcFWQsDI79y9+MI1EdWxIgBQi+MJ2QACwMeg',
 'Blair,',
 'Bryan,',
 'By',
 'Callans,',
 'Carr,',
 'Clapper,',
 'Content-Transfer-Encoding:',
 'Content-Type:',
 'Controllers"',
 'Darrell;',
 'Date:',
 'Eric"',
 'Exchange',
 'FW:',
 'From:',
 'Gary;',
 'Gas',
 'James;',
 'Jean;',
 'Jerry;',
 'Karen;',
 'Kathy;',
 'MIME-Version:',
 'Message-----',
 'Message-ID:',
 'Microsoft',
 'NAHOU-MSMBX01V.corp.enron.com',
 'NAHOU-MSMBX07V.corp.enron.com',
 'Nancy"',
 'Nancy.Callans@ENRON.com',
 'Nancy;',
 'Oct',
 'October',
 'Produced',
 'Randy;',
 'Received:',
 'Return-Path:',
 'SMTPSVC(5.0.2195.2966);',
 'SUN1017.xls',
 'Schoolcraft,',
 'Sent:',
 'Shirley',
 

In [52]:
# Finding the common words in all our 1000 mails...
file_words = []
for i in range(0,1000):
    file_name = 'DataSets' + '/' + new_df['paths'][i]
    
    with open(file_name,'r',encoding='utf-8',errors='ignore') as f:
        words = set(f.read().split())
        
        file_words.append(words)
        
common_words = set.intersection(*file_words)
print(common_words)

{'Received:', 'by', 'Microsoft'}


#### Adding `From` column

In [53]:
substring = 'From'
from_index = []

for i in range(0,1000):
    flag = True
    for string in lst_lst[i]:
        if substring in string:
            index = lst_lst[i].index(string)
            from_index.append(index)
            flag = False
            break
    
    if(flag):
        from_index.append(-1)
            
print(from_index)

[14, 16, 11, 30, 15, 16, 11, 14, 11, 19, 12, 14, 13, 11, 10, 10, 14, 17, 15, 15, 14, 11, 12, 14, 13, 12, 14, 13, 10, 15, 14, 14, 13, 17, 12, 14, 16, 11, 12, 14, 15, 14, 15, 14, 11, 22, 21, 20, 11, 20, 11, 13, 14, 17, 17, 11, -1, 13, 14, 14, 14, 11, 12, 12, 14, 14, 11, 13, 14, 14, 17, 11, 15, 14, 11, 14, 14, 14, 15, 10, 14, 12, 11, 12, 11, 17, 13, 12, 14, 17, 18, 12, 19, 20, 12, 11, 12, 14, 11, 14, 10, 14, 10, 12, 15, 12, 10, 14, 11, 12, 15, 11, 11, 14, 15, 12, 10, 22, -1, 14, 12, 10, 14, 14, 12, 15, 17, 11, 11, 12, 12, 15, 30, 14, 10, 14, 14, 11, 22, 15, 15, 14, 18, 11, 12, 11, 14, 12, 14, 11, 14, 12, 11, 14, 11, 11, 17, 12, 15, 17, 14, 12, 17, 14, 14, 11, 16, 13, 11, 12, 18, 11, 14, 13, 12, 12, 13, 13, 11, 13, 14, 12, 14, 11, 15, 26, 14, 16, 14, 11, 10, 14, 13, 17, 14, 13, 14, 10, 14, 14, 12, 12, 17, 12, 18, 14, 14, 11, 14, 11, 11, 14, 14, 12, 15, 10, 15, 15, 14, 12, 12, 12, 14, 19, 12, 14, 14, 11, 14, 13, 16, 13, 14, 17, 11, 17, 13, 13, 14, 11, 11, 14, 13, 14, 14, 19, 17, 17, 14, 11,

In [54]:
From = []

for i in range(0,1000):
    if(from_index[i] != -1): 
        From.append(lst_lst[i][from_index[i]][6:-1])
    else:
        From.append([])



In [55]:
new_df['From'] = From

In [56]:
new_df

label             path  \
0        0  ../data/082/117   
1        1  ../data/007/143   
2        1  ../data/252/079   
3        0  ../data/044/269   
4        1  ../data/004/207   
..     ...              ...   
995      1  ../data/004/259   
996      0  ../data/077/271   
997      0  ../data/077/130   
998      1  ../data/258/190   
999      1  ../data/255/107   

                                         file_contents  \
0    [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
1    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
2    [Received: from nahou-mscnx06p.corp.enron.com ...   
3    [Received: from nahou-mscnx06p.corp.enron.com ...   
4    [Recieved: from nahou-mscnx06p.corp.enron.com ...   
..                                                 ...   
995  [Recieved: from nahou-mscnx06p.corp.enron.com ...   
996  [Received: from nahou-mscnx03p.corp.enron.com ...   
997  [Received: from NAHOU-MSMBX07V.corp.enron.com ...   
998  [Received: from nahou-mscnx06p.corp.enron.com ...   
999  [Received: from nahou-mscnx06p.corp.enron.com ...   

                                               Subject         paths  \
0                                      FW: SUN1017.xls  data/082/117   
1                                              PRIVATE  data/007/143   
2                                                  Fw:  data/252/079   
3     OASIS Posting -  Revised Final Real Power Losses  data/044/269   
4                                                Marci  data/004/207   
..                                                 ...           ...   
995                                 are you suffering   data/004/259   
996                         RE: Off-site Presentations  data/077/271   
997                                           RE: Pira  data/077/130   
998  Need Protection against SARS viruses? This may...  data/258/190   
999                       What you've been looking for  data/255/107   

                                              From  
0       "Callans, Nancy" <Nancy.Callans@ENRON.com>  
1                "eric persson" <ericperss@web.de>  
2                 Nizadil <agarpina@scientist.com>  
3                                  rlstone@bpa.gov  
4    "Adrienne Wang" <IKATU@zippy.cs.columbia.edu>  
..                                             ...  
995           "Dorothy Mason" <wdnesc@gee-wiz.com>  
996       "Hirl, Joseph" <joseph.p.hirl@enron.com>  
997         "Zivic, Robyn" <Robyn.Zivic@ENRON.com>  
998    "Candy Vegas" <ubyfevkflyn@boardermail.com>  
999                       " Rosas" <fsipmuhiopgh@>  

[1000 rows x 6 columns]

In [57]:
from_index[995]

17

In [58]:
body_index = []

# list to store the major keywords....if this keywords occur remove that particular line....this way will reduce our data to 
# greater extent to obtain the 'body' of the mail...
temp = ['Received','Microsoft','From','Subject','To','Content-Type','Reply-To','Date','X-Priority','X-Mailer','Message-ID','X-Mailman-Version','MIME-Version'
,'Content-Transfer-Encoding']


In [59]:
body_lst = []
for i in range(len(lst_lst)):
    mail = lst_lst[i]
    for substring in mail:
        for x in temp:
            if x in substring:
#                 print(i)
#                 print(lst_lst[i].index(substring))
#                 print(lst_lst[i][lst_lst[i].index(substring)])
                indexs = lst_lst[i].index(substring)
#                 print("1")
                lst_lst[i].pop(indexs)
                break
    
    body_lst.append(lst_lst[i])

print(len(body_lst))
                

1000


In [60]:
lst_lst_copy = lst_lst.copy()

In [61]:
# body_lst_new = []

# for i,item in enumerate(lst_lst_copy):
#     for j,subItem in enumerate(item):
#         for k,subString in enumerate(temp):
#             if subString in subItem:
#                 lst_lst_copy[i].pop(j)
                    
#     body_lst_new.append(lst_lst_copy[i])
    

In [62]:
# print((body_lst_new[0]))

In [63]:
# Enumerate demonstration

ll = ['amman','chhetri','is','rich']
for i,item in enumerate(ll):
    print(i,item)

0 amman
1 chhetri
2 is
3 rich


In [64]:
new_df['body'] = body_lst

In [65]:
new_df

label             path  \
0        0  ../data/082/117   
1        1  ../data/007/143   
2        1  ../data/252/079   
3        0  ../data/044/269   
4        1  ../data/004/207   
..     ...              ...   
995      1  ../data/004/259   
996      0  ../data/077/271   
997      0  ../data/077/130   
998      1  ../data/258/190   
999      1  ../data/255/107   

                                         file_contents  \
0    [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   
1    [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...   
2    [\t Mon, 18 Mar 2002 04:42:27 -0800\n, \t Mon,...   
3    [\t Thu, 6 Sep 2001 09:07:26 -0700\n, \t Thu, ...   
4    [\t Thu, 12 Jul 2001 17:46:27 -0800\n, \t Thu,...   
..                                                 ...   
995  [\t Fri, 13 Jul 2001 02:22:51 -0800\n, \t Fri,...   
996  [\t Thu, 11 Oct 2001 17:45:54 -0500\n, \t Thu,...   
997  [\t Thu, 11 Oct 2001 11:05:48 -0500\n, content...   
998  [\t Fri, 29 Mar 2002 20:37:25 -0800\n, \t Fri,...   
999  [\t Sat, 23 Mar 2002 02:05:27 -0800\n, \t Sat,...   

                                               Subject         paths  \
0                                      FW: SUN1017.xls  data/082/117   
1                                              PRIVATE  data/007/143   
2                                                  Fw:  data/252/079   
3     OASIS Posting -  Revised Final Real Power Losses  data/044/269   
4                                                Marci  data/004/207   
..                                                 ...           ...   
995                                 are you suffering   data/004/259   
996                         RE: Off-site Presentations  data/077/271   
997                                           RE: Pira  data/077/130   
998  Need Protection against SARS viruses? This may...  data/258/190   
999                       What you've been looking for  data/255/107   

                                              From  \
0       "Callans, Nancy" <Nancy.Callans@ENRON.com>   
1                "eric persson" <ericperss@web.de>   
2                 Nizadil <agarpina@scientist.com>   
3                                  rlstone@bpa.gov   
4    "Adrienne Wang" <IKATU@zippy.cs.columbia.edu>   
..                                             ...   
995           "Dorothy Mason" <wdnesc@gee-wiz.com>   
996       "Hirl, Joseph" <joseph.p.hirl@enron.com>   
997         "Zivic, Robyn" <Robyn.Zivic@ENRON.com>   
998    "Candy Vegas" <ubyfevkflyn@boardermail.com>   
999                       " Rosas" <fsipmuhiopgh@>   

                                                  body  
0    [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...  
1    [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...  
2    [\t Mon, 18 Mar 2002 04:42:27 -0800\n, \t Mon,...  
3    [\t Thu, 6 Sep 2001 09:07:26 -0700\n, \t Thu, ...  
4    [\t Thu, 12 Jul 2001 17:46:27 -0800\n, \t Thu,...  
..                                                 ...  
995  [\t Fri, 13 Jul 2001 02:22:51 -0800\n, \t Fri,...  
996  [\t Thu, 11 Oct 2001 17:45:54 -0500\n, \t Thu,...  
997  [\t Thu, 11 Oct 2001 11:05:48 -0500\n, content...  
998  [\t Fri, 29 Mar 2002 20:37:25 -0800\n, \t Fri,...  
999  [\t Sat, 23 Mar 2002 02:05:27 -0800\n, \t Sat,...  

[1000 rows x 7 columns]

## The are Some of The Preprocessing Techniques we used whenver there is textual data ----

    1. Lower Casing
    2. Removal of Punctuations
    3. Removal of Stopwords in Text Pre-processing
    4. Removal of Frequent Words
    5. Stemming in Text Pre-processing 
    6. Lemmatization
    7. Conversion of Emoticons in Text Pre-processing
    8. Removal of URL’S
    9. Remove HTML tags
    10. Spelling Correction
    11. Removal of Rare words

In [66]:
new_df = new_df.rename(columns={'body':'Body'})
new_df.head(2)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   
1      1  ../data/007/143  [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   
1          PRIVATE  data/007/143           "eric persson" <ericperss@web.de>   

                                                Body  
0  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...  
1  [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...

In [67]:
## Here we will apply some of these methods in both the columns ie. 'Subject' and 'Body' .. 

#### Applying on `Body`

In [68]:
# stop

#### 1. Lower Casing

In [69]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  
0  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...

In [70]:
def to_string(text):
    return "".join([i for i in text])

new_df['Body'] = new_df['Body'].map(to_string)

In [71]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  
0  \t Tue, 16 Oct 2001 09:21:42 -0500\ncontent-cl...

In [72]:
# def to_lower(text):
#     if(len(text) == 0):
#         pass
#     else:
#         text.lower()
        
new_df['Body'] = new_df['Body'].apply(lambda x : x.lower())
new_df.head(2)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   
1      1  ../data/007/143  [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   
1          PRIVATE  data/007/143           "eric persson" <ericperss@web.de>   

                                                Body  
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...  
1  \t tue, 17 jul 2001 06:06:54 -0800\n\t tue, 17...

In [73]:
type(new_df['Body'][0])

str

#### 2. Removal of Punctuations

In [74]:
# Listing all punctuations present in the string library
import string
print(string.punctuation)

!"#$%&'()*+,-./:;<=>?@[\]^_`{|}~


In [75]:
def remove_punctuation(text):
    punctuation_free = ""
    for i in text:
        if i not in string.punctuation:
            punctuation_free += i
        else:
            continue

    return punctuation_free



# Above function can also be written as 
def remove_punctuation(text):
    punctuation_free = "".join([i for i in text if i not in string.punctuation])
    return punctuation_free

In [76]:
new_df['Body_after_punctuation_removal'] = new_df['Body'].apply(lambda x : remove_punctuation(x))
new_df.head(2)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   
1      1  ../data/007/143  [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   
1          PRIVATE  data/007/143           "eric persson" <ericperss@web.de>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   
1  \t tue, 17 jul 2001 06:06:54 -0800\n\t tue, 17...   

                      Body_after_punctuation_removal  
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...  
1  \t tue 17 jul 2001 060654 0800\n\t tue 17 jul ...

In [77]:
x = new_df['Body_after_punctuation_removal']
y = new_df['label']

In [78]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)

vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

y_pred = nb_classifier.predict(x_test_vectorized)


accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  98.28571428571429


#### Removal of Stopwords in Text-Preprocessing

In [79]:
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
",".join(stopwords.words('english'))

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\91747\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


"i,me,my,myself,we,our,ours,ourselves,you,you're,you've,you'll,you'd,your,yours,yourself,yourselves,he,him,his,himself,she,she's,her,hers,herself,it,it's,its,itself,they,them,their,theirs,themselves,what,which,who,whom,this,that,that'll,these,those,am,is,are,was,were,be,been,being,have,has,had,having,do,does,did,doing,a,an,the,and,but,if,or,because,as,until,while,of,at,by,for,with,about,against,between,into,through,during,before,after,above,below,to,from,up,down,in,out,on,off,over,under,again,further,then,once,here,there,when,where,why,how,all,any,both,each,few,more,most,other,some,such,no,nor,not,only,own,same,so,than,too,very,s,t,can,will,just,don,don't,should,should've,now,d,ll,m,o,re,ve,y,ain,aren,aren't,couldn,couldn't,didn,didn't,doesn,doesn't,hadn,hadn't,hasn,hasn't,haven,haven't,isn,isn't,ma,mightn,mightn't,mustn,mustn't,needn,needn't,shan,shan't,shouldn,shouldn't,wasn,wasn't,weren,weren't,won,won't,wouldn,wouldn't"

In [80]:
# before removal of stopwords we need to tokenize text

# defining function for tokenization
import re
from nltk.tokenize import WhitespaceTokenizer

def tokenization(text):
    tk = WhitespaceTokenizer()
    return tk.tokenize(text)

new_df['tokenized_Body'] = new_df['Body_after_punctuation_removal'].apply(lambda x : tokenization(x))

In [81]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...

In [82]:
# Now StopWords Removal

# importing nlp library
import nltk
nltk.download('stopwords')

stopwords = nltk.corpus.stopwords.words('english')

# defining the function to remove stopwords from tokenized text
def remove_stopwords(text):
    output = [i for i in text if i not in stopwords]
    return output

#applying the function for removal of stopwords
new_df['Body_after_stopWords_removal'] = new_df['tokenized_Body'].apply(lambda x : remove_stopwords(x))

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\91747\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [83]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...

In [84]:
# # Temporary 

# def dryrun(value):
#     txt = " ".join([i for i in value])
#     return txt
    
    
# new_df['temp'] = new_df['Subject_after_stopWords_removal'].map(dryrun)

In [85]:
# Temporary 

def dryrun(value):
    txt = " ".join([i for i in value])
    return txt
    
    
new_df['temp'] = new_df['Body_after_stopWords_removal'].map(dryrun)

In [86]:
x = new_df['temp']
y = new_df['label']

In [87]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)

vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

y_pred = nb_classifier.predict(x_test_vectorized)


accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  99.85714285714286


### Removal of Frequent Words
<!-- 
<!-- Here we have to be careful because....sometimes a subject is made up only of the frequent words or stop words...and removing the frequent words or stopwords  may make the subject as an empty
string...which will cause trouble.. --> -->


###### Here in this scenario if we are removing the frequent words from the mails...then we are getting string only containing stopwords for some subjects...thats ###### why we wont use this technique here...

In [88]:
# It's better to remove the most frequent words sometimes...
from collections import Counter
cnt = Counter()
for text in new_df['Body_after_stopWords_removal'].values:
    for word in text:
        cnt[word] += 1


# It will return the most common words in the whole 1000 mails ...in the list of pairs format ie. [('a',32),('c',12)] ..where the first element of each pair 
# represents the specific word...and the second element of the pair represent the respective count of the word..

cnt.most_common(10)


FREQWORDS = set([w for (w,wc) in cnt.most_common(10)])

def remove_freqwords(text):
    """ Custom function to remove freq words """
    return " ".join([word for word in text if word not in FREQWORDS])

new_df['Body_after_frequentWords_removal'] = new_df['Body_after_stopWords_removal'].apply(lambda x : remove_freqwords(x))

In [89]:
# new_df.head(5)

In [90]:
x = new_df['Body_after_frequentWords_removal']
y = new_df['label']

In [91]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)

vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

y_pred = nb_classifier.predict(x_test_vectorized)


accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  99.14285714285714


#### Stemming in Text Pre-Processing

    It is a text standardization technique where a word is reduced to its stem/base word. Example: “jabbing” → “jab” and “kicking” → “kick”. The main aim for stemming is that we can reduce the vocab size before inputting it into any machine learning  model.

In [92]:
#importing the Stemming function from nltk Library
from nltk.stem.porter import PorterStemmer

#defining the object for stemming
porter_stemmer = PorterStemmer()

#defining a function for stemming
def stemming(text):
    stem_text = [porter_stemmer.stem(word) for word in text]
    return stem_text

#applying function for stemming
new_df["Body_after_Stemming"] = new_df['Body_after_stopWords_removal'].apply(lambda x : stemming(x))

new_df.head(1)


label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...

In [93]:
# Temporary 

def dryrun(value):
    txt = " ".join([i for i in value])
    return txt
    
    
new_df['temp'] = new_df['Body_after_Stemming'].map(dryrun)

In [94]:
x = new_df['temp']
y = new_df['label']

In [95]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...

In [96]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)

vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

y_pred = nb_classifier.predict(x_test_vectorized)


accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  99.71428571428571


In [97]:
# stop

new_df.head(3)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   
1      1  ../data/007/143  [\t Tue, 17 Jul 2001 06:06:54 -0800\n, \t Tue,...   
2      1  ../data/252/079  [\t Mon, 18 Mar 2002 04:42:27 -0800\n, \t Mon,...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   
1          PRIVATE  data/007/143           "eric persson" <ericperss@web.de>   
2              Fw:  data/252/079            Nizadil <agarpina@scientist.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   
1  \t tue, 17 jul 2001 06:06:54 -0800\n\t tue, 17...   
2  \t mon, 18 mar 2002 04:42:27 -0800\n\t mon, 18...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   
1  \t tue 17 jul 2001 060654 0800\n\t tue 17 jul ...   
2  \t mon 18 mar 2002 044227 0800\n\t mon 18 mar ...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   
1  [tue, 17, jul, 2001, 060654, 0800, tue, 17, ju...   
2  [mon, 18, mar, 2002, 044227, 0800, mon, 18, ma...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   
1  [tue, 17, jul, 2001, 060654, 0800, tue, 17, ju...   
2  [mon, 18, mar, 2002, 044227, 0800, mon, 18, ma...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   
1  tue 17 jul 2001 060654 0800 tue 17 jul 2001 08...   
2  mon 18 mar 2002 044227 0800 mon 18 mar 2002 06...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   
1  tue 17 jul 060654 0800 tue 17 jul 080520 conte...   
2  mon 18 044227 0800 mon 18 064031 content techn...   

                                 Body_after_Stemming  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...  
1  [tue, 17, jul, 2001, 060654, 0800, tue, 17, ju...  
2  [mon, 18, mar, 2002, 044227, 0800, mon, 18, ma...

#### Lemmatization
    . Lemmatization is very similar to stemming with the only difference being the word here will get reduced to a word that has  a particular meaning in its language. Due to this, lemmatization is generally slower than stemming.
    .Let us use the WordNetLemmatizer in nltk to lemmatize our sentences.

In [98]:
a = 'amman Chhetri'
for word in a.split():
    print(word)

amman
Chhetri


In [99]:
# for i in range(0,1000):
#     print(new_df['Subject_after_Stemming'][i])

In [100]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...

In [101]:
# new_df['Subject_after_Stemming'][0]
# type(new_df['temp'][0])

# def to_string(text):
#     for word in text:
#         return " ".join(word)
    
# new_df['Subject_after_Stemming'] = new_df['temp'].apply(to_string)

# new_df.head(5)

In [102]:
# # Temporary 

# def dryrun(value):
#     txt = " ".join([i for i in value])
#     return txt
    
    
# new_df['temp'] = new_df['Subject_after_Stemming'].map(dryrun)

In [103]:
import nltk
nltk.download('wordnet')

from nltk.stem import WordNetLemmatizer

lemmatizer = WordNetLemmatizer()

# for using the text.split() ...we need the text to be in string format...
def lemmatize_words(text):
    return " ".join([lemmatizer.lemmatize(word) for word in text.split()])

new_df["Body_after_lemmatizing"] = new_df['temp'].apply(lambda x : lemmatize_words(x))


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\91747\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [104]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

In [105]:
x = new_df['Body_after_lemmatizing']
y = new_df['label']

x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)

vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

y_pred = nb_classifier.predict(x_test_vectorized)

accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  99.71428571428571


In [106]:
# stop

#### Removal of URL's 

In [107]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

In [108]:
# Temporary 

def dryrun(value):
    txt = " ".join([i for i in value])
    return txt
    
    
new_df['temp'] = new_df['Body_after_lemmatizing'].map(dryrun)



In [109]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  t u e   1 6   o c t   2 0 0 1   0 9 2 1 4 2   ...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

In [110]:
def remove_urls(text):
    url_pattern = re.compile(r'https?://\S+\www\.\S+')
    return url_pattern.sub(r'',text)


new_df["Body_after_removing_URLs"] = new_df['Body_after_lemmatizing'].apply(lambda x : remove_urls(x))

In [111]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  t u e   1 6   o c t   2 0 0 1   0 9 2 1 4 2   ...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                            Body_after_removing_URLs  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

In [112]:
# def to_string(text):
#     for i in range(0,1000):
#         if (type(new_df["cleaned_tokens_Subject"][i]) == str):
#             return new_df["cleaned_tokens_Subject"][i]
#         else:
#             return str(new_df["cleaned_tokens_Subject"][i])
        
        
# new_df["cleaned_tokens_Subject"] = new_df["cleaned_tokens_Subject"].apply(lambda x : to_string(text))

# new_df.head(7)

### Removal of `HTML` tags

In [113]:
def remove_html(text):
    html_pattern = re.compile('<.*?>')
    return html_pattern.sub(r'',text)


new_df['Body_after_removing_HTML_tags'] = new_df['Body_after_removing_URLs'].map(remove_html)

In [114]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  t u e   1 6   o c t   2 0 0 1   0 9 2 1 4 2   ...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                            Body_after_removing_URLs  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                       Body_after_removing_HTML_tags  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

### Spelling Correction

In [115]:
# from spellchecker import SpellChecker


# spell = SpellChecker()

# def correct_spelling(text):
#     corrected_text = []
#     mispelled_words = spell.unknown(text.split())
#     for word in text.split():
#         if word in mispelled_words:
#             corrected_text.append(spell.correction(word))
#         else:
#             corrected_text.append(word)
#     return " ".join(corrected__text)

 

### Removal of `Rare Words`  

In [116]:
from collections import Counter
cnt = Counter()

for text in new_df['Body_after_removing_HTML_tags'].values:
    for word in text:
        cnt[word] += 1
        
n_rare_words = 10

Rare_words = set([w for (w,wc) in cnt.most_common()[:-n_rare_words-1:-1]])

def remove_rarewords(text):
    return " ".join([word for word in str(text).split() if word not in Rare_words])

In [117]:
new_df['Body_after_removing_Rare_Words'] = new_df['Body_after_removing_HTML_tags'].map(remove_rarewords)

In [118]:
new_df.head(1)

label             path                                      file_contents  \
0      0  ../data/082/117  [\t Tue, 16 Oct 2001 09:21:42 -0500\n, content...   

           Subject         paths                                        From  \
0  FW: SUN1017.xls  data/082/117  "Callans, Nancy" <Nancy.Callans@ENRON.com>   

                                                Body  \
0  \t tue, 16 oct 2001 09:21:42 -0500\ncontent-cl...   

                      Body_after_punctuation_removal  \
0  \t tue 16 oct 2001 092142 0500\ncontentclass u...   

                                      tokenized_Body  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                        Body_after_stopWords_removal  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                                                temp  \
0  t u e   1 6   o c t   2 0 0 1   0 9 2 1 4 2   ...   

                    Body_after_frequentWords_removal  \
0  tue 16 oct 092142 contentclass urncontentclass...   

                                 Body_after_Stemming  \
0  [tue, 16, oct, 2001, 092142, 0500, contentclas...   

                              Body_after_lemmatizing  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                            Body_after_removing_URLs  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                       Body_after_removing_HTML_tags  \
0  tue 16 oct 2001 092142 0500 contentclass urnco...   

                      Body_after_removing_Rare_Words  
0  tue 16 oct 2001 092142 0500 contentclass urnco...

In [119]:
# # Temporary 

# def dryrun(value):
#     txt = " ".join([i for i in value])
#     return txt
    
    
# new_df['temp'] = new_df['Subject_after_Stemming'].map(dryrun)

In [120]:
# helper - code to find the number of rows containing empty string in the temp column...

empty_subject = []

for x in new_df['temp']:
    if x == '':
        empty_subject.append(x)
        
len(empty_subject) 
     

0

In [ ]:
# new_df['temp'].value_counts()

In [122]:
x = new_df['Body_after_removing_Rare_Words']
y = new_df['label']

In [123]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.3,random_state=42)


In [124]:
vectorizer = CountVectorizer()
x_train_vectorized = vectorizer.fit_transform(x_train)
x_test_vectorized = vectorizer.transform(x_test)

In [125]:
nb_classifier = MultinomialNB(alpha=10,fit_prior=False)
nb_classifier.fit(x_train_vectorized,y_train)

MultinomialNB(alpha=10, fit_prior=False)

### Training

In [136]:
y_pred = nb_classifier.predict(x_test_vectorized)


In [139]:
from sklearn.metrics import classification_report

print(classification_report(y_test,y_pred))

              precision    recall  f1-score   support

           0       0.99      0.99      0.99       157
           1       0.99      0.99      0.99       143

    accuracy                           0.99       300
   macro avg       0.99      0.99      0.99       300
weighted avg       0.99      0.99      0.99       300



In [140]:
len(y_test),len(y_pred)

(300, 300)

In [144]:
accuracy = accuracy_score(y_test,y_pred)
print("Accuracy : ",accuracy*100)

Accuracy :  99.0
